# TP 2-3 : Branch-and-bound applied to a knapsack problem

### Initialisation (à faire une seule fois)

In [2]:
import Pkg; 
Pkg.add("GraphRecipes"); Pkg.add("Plots"); 
using GraphRecipes, Plots #only used to visualize the search tree at the end of the branch-and-bound

    Updating registry at `~/.julia/registries/General`
   Resolving package versions...
  No Changes to `~/.julia/environments/v1.6/Project.toml`
  No Changes to `~/.julia/environments/v1.6/Manifest.toml`
   Resolving package versions...
  No Changes to `~/.julia/environments/v1.6/Project.toml`
  No Changes to `~/.julia/environments/v1.6/Manifest.toml`


### Récupération des données

In [9]:
function readKnapInstance(filename)
    price=[]
    weight=[]
    capacity = -1
    open(filename) do f
        for i in 1:3
            tok = split(readline(f))
            if (tok[1] == "ListPrices=")
                for i in 2:(length(tok)-1)
                    push!(price,parse(Int64, tok[i]))
                end
            elseif (tok[1] == "ListWeights=")
                for i in 2:(length(tok)-1)
                    push!(weight,parse(Int64, tok[i]))
                end
            elseif (tok[1] == "Capacity=")
                capacity = parse(Int64, tok[2])
            else
                println("Unknown read :", tok)
            end 
        end
    end
    
    return price, weight, capacity
end

# readKnapInstance("data/test.opb")
# readKnapInstance("data/almost_strongly_correlated/knapPI_5_50_1000_1_-2096.opb")

(Any[42, 40, 12, 25], Any[7, 4, 3, 5], 10)

### Procédure d'application des tests de sondabilités TA, TO et TR pour le cas de la relaxation linéaire

In [4]:
function TestsSondabilite_relaxlin(x, price, weight, capacity, varsbin, BestProfit, Bestsol)
    TA, TO, TR = false, false, false
    if (!Constraints(x, weight, capacity)) # Test de faisabilite
        TA = true
        println("TA")
    elseif (Objective(x, price) <= BestProfit) # Test d'optimalite
        TO = true
        println("TO")
    elseif (AllDef(x)) # Test de resolution
        TR = true
        println("TR")
        #if (value(benef) >= BestProfit)
        if (Objective(x, price) >= BestProfit)
            Bestsol = x
            #BestProfit=value(benef)
            BestProfit = Objective(x, price)
        end
    else
        println("non sondable")
    end
    TA, TO, TR, Bestsol, BestProfit
end

TestsSondabilite_relaxlin (generic function with 1 method)

### Procédure de séparation et stratégie d'exploration permettant de se placer au prochain noeud à traiter

In [5]:

function SeparerNoeud_relaxlin(varsshouldbebinary, listvars, listvals)
    # le noeud est non-sondable. Appliquer le critère de séparation pour le séparer en sous-noeuds et choisir un noeud-fils le plus à gauche   
    
    # Cas du noeud le plus à gauche
    predX = first(listvars)
    nextX0 = predX
    for xi in predX
        
    end


    push!(listvars,var) #stocker l'identite de la variable choisie pour la séparation
    push!(listvals,1.0) #stocker la branche choisie, identifiee par la valeur de la variable choisie
    listvars, listvals
end


function ExplorerAutreNoeud_relaxlin(listvars, listvals, listnodes)
    #this node is sondable, go back to parent node then right child if possible
    
    stop=false
    #check if we are not at the root node
    if (length(listvars)>= 1)
        #go back to parent node
        var=pop!(listvars)
        theval=pop!(listvals)
        tmp=pop!(listnodes)
        set_lower_bound(var,0.0)
        set_upper_bound(var,1.0)

        #go to right child if possible, otherwise go back to parent
        while ( (theval==0.0) && (length(listvars)>= 1))
            var=pop!(listvars)
            theval=pop!(listvals)
            tmp=pop!(listnodes)
            set_lower_bound(var,0.0) 
            set_upper_bound(var,1.0)
        end
        if theval==1.0
            set_lower_bound(var,0.0)
            set_upper_bound(var,0.0)
            push!(listvars,var)
            push!(listvals,0.0)
        else
            println("\nFINISHED")
            stop=true
        end
    else
        #the root node was sondable
        println("\nFINISHED")
        stop=true
    end
    listvars, listvals, listnodes, stop 
end

ExplorerAutreNoeud_relaxlin (generic function with 1 method)

In [10]:
# fonction objectif que l'on souhaite maximiser/minimiser
Objective(x, price) = 
    sum(
        if x[i] < 0
            1
        else
            price[i]*x[i] 
        end
            for i in 1:length(x)
    )

# fonction permettant de vérfier toutes les contraintes du modèle
Constraints(x, weight, capacity) =
    sum(
        if x[i] < 0
            0
        else 
            weight[i]*x[i]
        end
            for i in 1:length(x)
    ) <= capacity


AllDef(x) =
    for xi in x
        if xi < 0
            return false
        end
    end
    return true

Constraints (generic function with 1 method)